In [0]:
# set whether normal process or being run by Elsevier supporters
permissions='fulldata' # default or fulldata
# set the project name
project_name = 'test_project_1'  # This is the folder name that you work in, e.g. 'test_project_1'

In [0]:
%run /Snippets/header_008

PROJECT DETAILS:
Project identifier: test_project_1
Cluster data access level: fulldata


EXECUTION DETAILS:
Spark version: 11.3.x-scala2.12, 
Cluster Node Type: i3.xlarge, 
Driver Node Type: c4.2xlarge, 
Worker Node Type: i3.xlarge


In [0]:
import pandas as pd
import numpy as np
import pyspark.pandas as ps
from pyspark.sql import SparkSession
from pyspark.sql.window import Window
from pyspark.sql.functions import monotonically_increasing_id, row_number, coalesce, countDistinct

DATA SNAPSHOT DETAILS:
This notebook uses the latest snapshot date for this version: "v008.20221021151538/", (21 October 2022)

 The following are the Scopus snapshot dates available for datasets at v008:
['v008.20220314092239/', 'v008.20220906063204/', 'v008.20221021151538/']
(If you want to use a different snapshot, in the first cell of your notebook, set the variable `custom_snapshot_date` to one of the options listed above (string data type))



DATA SAMPLE DETAILS:
Setting paths to run on full datasets (100% Scopus publication volume)


In [0]:
data_scival = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/wgu53@wisc.edu/parent_scival.csv")
data_aff_parent = spark.read.format("csv").option("header", "true").load("s3://elsevier-fcads-icsrlabdatabricks/custom/proj_030_facmob/aff_parent_final.csv"))

In [0]:
df_ipr = spark.read.format("parquet").load(basePath + tablename_ipr)

integrate data from former two affiliation_paretn together to get the final version of affiliation parent

In [0]:
data_scival = data_scival.withColumnRenamed("afid",'scival_afid').withColumn('key',func.col('scival_afid'))
data_scival.display()

scival_afid parent_afid key 60088055 60001681 60088055 60107243 60001681 60107243 60112942 60001681 60112942 60076841 60076509 60076841 60091248 60076509 60091248 60077546 60018290 60077546 60009515 60018290 60009515 60077754 60032170 60077754 60010254 60013913 60010254 60090476 60013913 60090476 60017857 60002457 60017857 60007950 60002457 60007950 60018924 60026478 60018924 60026934 60026478 60026934 60000404 60026478 60000404 60015984 60026478 60015984 60101197 60026478 60101197 60023357 60074952 60023357 60096653 60074952 60096653 60074963 60074952 60074963 60102609 60074952 60102609 60088241 60074952 60088241 60007207 60074952 60007207 60012109 60074952 60012109 60012234 60074952 60012234 60006722 60074952 60006722 60021637 60016159 60021637 60077302 60002583 60077302 60011035 60024780 60011035 60011972 60019228 60011972 60021706 60019228 60021706 60001982 60019228 60001982 60024076 60009503 60024076 60016853 60010352 60016853 60010630 60010352 60010630 60013487 60010352 60013487 60009836 60010352 60009836 60021390 60007977 60021390 60018858 60108065 60018858 60019750 60005873 60019750 60014566 60003515 60014566 60006157 60003515 60006157 60030001 60025500 60030001 60008883 60025500 60008883 60075105 60025236 60075105 60111163 60111165 60111163 60006191 60111165 60006191 60116922 60111165 60116922 60111160 60111165 60111160 60026044 60005407 60026044 60023512 60005407 60023512 60005540 60005407 60005540 60028182 60024586 60028182 60100743 60100742 60100743 60026719 60000787 60026719 60000407 60024727 60000407 60025374 60015791 60025374 60003861 60015791 60003861 60028530 60007161 60028530 60006713 60007161 60006713 60010624 60007161 60010624 60018398 60017635 60018398 60010820 60017635 60010820 60013444 60017635 60013444 60025717 60026798 60025717 60008994 60026798 60008994 60012559 60026798 60012559 60001075 60013357 60001075 60000200 60022606 60000200 60028443 60011425 60028443 60116324 60020420 60116324 60018591 60016943 60018591 60000003 60016943 60000003 60010549 60016943 60010549 60015052 60016943 60015052 60021048 60001673 60021048 60113039 60113038 60113039 60017387 60014715 60017387 60025095 60000451 60025095 60004087 60012222 60004087 60022481 60017205 60022481 60077130 60074592 60077130 60026566 60008040 60026566 60093643 60008040 60093643 60020067 60008040 60020067 60015864 60003892 60015864 60004372 60003892 60004372 60004683 60003892 60004683 60003699 60003892 60003699 60086304 60003892 60086304 60093724 60003892 60093724 60093787 60003892 60093787 60093807 60003892 60093807 60009043 60003892 60009043 60093810 60003892 60093810 60116796 60003892 60116796 60012562 60003892 60012562 60116379 60003892 60116379 60016091 60030639 60016091 60103035 60031934 60103035 60031532 60017640 60031532 60028618 60010256 60028618 60008335 60012960 60008335 60006481 60014300 60006481 60079146 60014300 60079146 60024136 60014300 60024136 60008383 60014300 60008383 60012230 60014300 60012230 60004458 60014300 60004458 60027826 60008853 60027826 60023694 60011754 60023694 60018384 60011754 60018384 60013674 60011754 60013674 60010469 60011754 60010469 60001085 60011754 60001085 60031288 60011754 60031288 60009974 60011754 60009974 60075002 60011754 60075002 60027574 60004819 60027574 60014801 60105348 60014801 60024399 60105348 60024399 60007872 60029246 60007872 60023432 60029246 60023432 60033488 60029246 60033488 60015593 60017974 60015593 60024457 60017974 60024457 60030633 60013567 60030633 60002381 60013567 60002381 60012097 60013567 60012097 60005258 60013567 60005258 60012977 60015958 60012977 60102851 60025086 60102851 60102854 60025086 60102854 60024444 60025086 60024444 60000988 60025086 60000988 60102852 60025086 60102852 60003259 60025086 60003259 60006519 60025086 60006519 60102853 60025086 60102853 60102855 60025086 60102855 60001749 60025086 60001749 60093657 60025086 60093657 60018485 60025086 60018485 60077094 60025086 60077094 60010211 60025086 60010211 60025207 60010171 60025207 60002365 60010171 60002365 600

In [0]:
parent_0 = data_aff_parent.select('afid','parent_final').withColumn('key',func.col('parent_final'))
parent_0.display()

afid parent_final key 103035115 60000027 60000027 125865588 60000027 60000027 107099789 60000027 60000027 103035114 60000027 60000027 125865724 60000027 60000027 105302540 60000027 60000027 103035124 60000027 60000027 125865723 60000027 60000027 125865444 60000027 60000027 125865722 60000027 60000027 107576527 60000027 60000027 103035123 60000027 60000027 103035119 60000027 60000027 112190034 60000027 60000027 114537697 60000027 60000027 113800358 60000027 60000027 125865589 60000027 60000027 122906263 60000027 60000027 121113920 60000027 60000027 107576528 60000027 60000027 125866024 60000027 60000027 125865819 60000027 60000027 125865821 60000027 60000027 125866081 60000027 60000027 126360461 60000027 60000027 125865719 60000027 60000027 114202984 60000027 60000027 114156031 60000027 60000027 103035125 60000027 60000027 106483728 60000027 60000027 106936439 60000027 60000027 126177098 60000027 60000027 103035116 60000027 60000027 106146977 60000027 60000027 113857772 60000027 60000027 103035118 60000027 60000027 103035111 60000027 60000027 103035117 60000027 60000027 125866080 60000027 60000027 106902853 60000027 60000027 125865725 60000027 60000027 124820720 60000027 60000027 125865961 60000027 60000027 125865887 60000027 60000027 114450524 60000027 60000027 106936440 60000027 60000027 118219740 60000027 60000027 108045255 60000027 60000027 103035122 60000027 60000027 107959373 60000027 60000027 125865446 60000027 60000027 103035113 60000027 60000027 125866025 60000027 60000027 105520429 60000027 60000027 125866023 60000027 60000027 125865443 60000027 60000027 114545997 60000027 60000027 60000027 60000027 60000027 119774456 60000027 60000027 125865587 60000027 60000027 125865888 60000027 60000027 106936438 60000027 60000027 119629621 60000027 60000027 109702401 60000027 60000027 103035121 60000027 60000027 116521488 60000027 60000027 108134393 60000027 60000027 125865442 60000027 60000027 125865889 60000027 60000027 126177099 60000027 60000027 116323654 60000027 60000027 125865720 60000027 60000027 106810721 60000027 60000027 123077533 60000027 60000027 108388592 60000027 60000027 125865590 60000027 60000027 110908040 60000027 60000027 103035110 60000027 60000027 125865721 60000027 60000027 128460063 60000027 60000027 112919916 60000027 60000027 106570589 60000027 60000027 125865445 60000027 60000027 123461275 60000027 60000027 114549264 60000027 60000027 125865818 60000027 60000027 118226097 60000027 60000027 118016425 60000027 60000027 125865820 60000027 60000027 103035112 60000027 60000027 107576529 60000027 60000027 125866082 60000027 60000027 103035126 60000027 60000027 125865817 60000027 60000027 114063503 60000027 60000027 106170824 60000027 60000027 103035120 60000027 60000027 127772984 60000027 60000027 103035367 60000035 60000035 103035365 60000035 60000035 103035370 60000035 60000035 106177616 60000035 60000035 116636451 60000035 60000035 108180138 60000035 60000035 103035360 60000035 60000035 103035354 60000035 60000035 60000035 60000035 60000035 103035358 60000035 60000035 103035357 60000035 60000035 103035353 60000035 60000035 118965332 60000035 60000035 119859752 60000035 60000035 103035366 60000035 60000035 116566667 60000035 60000035 116346307 60000035 60000035 103035356 60000035 60000035 103035364 60000035 60000035 114344029 60000035 60000035 114067201 60000035 60000035 103035362 60000035 60000035 103035355 60000035 60000035 118965331 60000035 60000035 103035371 60000035 60000035 103035368 60000035 60000035 128414031 60000035 60000035 117898642 60000035 60000035 120463241 60000035 60000035 103035359 60000035 60000035 118603812 60000035 60000035 113431186 60000035 60000035 122085983 60000035 60000035 122175321 60000035 60000035 125686706 60000035 60000035 126575643 60000035 60000035 120701644 60000071 60000071 115613983 60000071 60000071 103037633 60000071 60000071 103037630 60000071 60000071 109160891 60000071 60000071 105251920 60000071 60000071 103037595 60000071 60000071 118841640 60000071 60000071 1030

In [0]:
parent_1 = parent_0.join(data_scival,'key','left')
parent_1.display()

key afid parent_final scival_afid parent_afid 60000027 103035115 60000027 null null 60000027 125865588 60000027 null null 60000027 107099789 60000027 null null 60000027 103035114 60000027 null null 60000027 125865724 60000027 null null 60000027 105302540 60000027 null null 60000027 103035124 60000027 null null 60000027 125865723 60000027 null null 60000027 125865444 60000027 null null 60000027 125865722 60000027 null null 60000027 107576527 60000027 null null 60000027 103035123 60000027 null null 60000027 103035119 60000027 null null 60000027 112190034 60000027 null null 60000027 114537697 60000027 null null 60000027 113800358 60000027 null null 60000027 125865589 60000027 null null 60000027 122906263 60000027 null null 60000027 121113920 60000027 null null 60000027 107576528 60000027 null null 60000027 125866024 60000027 null null 60000027 125865819 60000027 null null 60000027 125865821 60000027 null null 60000027 125866081 60000027 null null 60000027 126360461 60000027 null null 60000027 125865719 60000027 null null 60000027 114202984 60000027 null null 60000027 114156031 60000027 null null 60000027 103035125 60000027 null null 60000027 106483728 60000027 null null 60000027 106936439 60000027 null null 60000027 126177098 60000027 null null 60000027 103035116 60000027 null null 60000027 106146977 60000027 null null 60000027 113857772 60000027 null null 60000027 103035118 60000027 null null 60000027 103035111 60000027 null null 60000027 103035117 60000027 null null 60000027 125866080 60000027 null null 60000027 106902853 60000027 null null 60000027 125865725 60000027 null null 60000027 124820720 60000027 null null 60000027 125865961 60000027 null null 60000027 125865887 60000027 null null 60000027 114450524 60000027 null null 60000027 106936440 60000027 null null 60000027 118219740 60000027 null null 60000027 108045255 60000027 null null 60000027 103035122 60000027 null null 60000027 107959373 60000027 null null 60000027 125865446 60000027 null null 60000027 103035113 60000027 null null 60000027 125866025 60000027 null null 60000027 105520429 60000027 null null 60000027 125866023 60000027 null null 60000027 125865443 60000027 null null 60000027 114545997 60000027 null null 60000027 60000027 60000027 null null 60000027 119774456 60000027 null null 60000027 125865587 60000027 null null 60000027 125865888 60000027 null null 60000027 106936438 60000027 null null 60000027 119629621 60000027 null null 60000027 109702401 60000027 null null 60000027 103035121 60000027 null null 60000027 116521488 60000027 null null 60000027 108134393 60000027 null null 60000027 125865442 60000027 null null 60000027 125865889 60000027 null null 60000027 126177099 60000027 null null 60000027 116323654 60000027 null null 60000027 125865720 60000027 null null 60000027 106810721 60000027 null null 60000027 123077533 60000027 null null 60000027 108388592 60000027 null null 60000027 125865590 60000027 null null 60000027 110908040 60000027 null null 60000027 103035110 60000027 null null 60000027 125865721 60000027 null null 60000027 128460063 60000027 null null 60000027 112919916 60000027 null null 60000027 106570589 60000027 null null 60000027 125865445 60000027 null null 60000027 123461275 60000027 null null 60000027 114549264 60000027 null null 60000027 125865818 60000027 null null 60000027 118226097 60000027 null null 60000027 118016425 60000027 null null 60000027 125865820 60000027 null null 60000027 103035112 60000027 null null 60000027 107576529 60000027 null null 60000027 125866082 60000027 null null 60000027 103035126 60000027 null null 60000027 125865817 60000027 null null 60000027 114063503 60000027 null null 60000027 106170824 60000027 null null 60000027 103035120 60000027 null null 60000027 127772984 60000027 null null 60000035 103035367 60000035 null null 60000035 103035365 60000035 null null 60000035 103035370 60000035 null null 60000035 106177616 60000035 null null 60000035 116636451 60000035 null null 60000035 108180138 60000035 null null 600

In [0]:
parent_2 = parent_1.withColumn('parent_afid',coalesce('parent_afid', 'parent_final'))
parent_2.display()

key afid parent_final scival_afid parent_afid 60000027 103035115 60000027 null 60000027 60000027 125865588 60000027 null 60000027 60000027 107099789 60000027 null 60000027 60000027 103035114 60000027 null 60000027 60000027 125865724 60000027 null 60000027 60000027 105302540 60000027 null 60000027 60000027 103035124 60000027 null 60000027 60000027 125865723 60000027 null 60000027 60000027 125865444 60000027 null 60000027 60000027 125865722 60000027 null 60000027 60000027 107576527 60000027 null 60000027 60000027 103035123 60000027 null 60000027 60000027 103035119 60000027 null 60000027 60000027 112190034 60000027 null 60000027 60000027 114537697 60000027 null 60000027 60000027 113800358 60000027 null 60000027 60000027 125865589 60000027 null 60000027 60000027 122906263 60000027 null 60000027 60000027 121113920 60000027 null 60000027 60000027 107576528 60000027 null 60000027 60000027 125866024 60000027 null 60000027 60000027 125865819 60000027 null 60000027 60000027 125865821 60000027 null 60000027 60000027 125866081 60000027 null 60000027 60000027 126360461 60000027 null 60000027 60000027 125865719 60000027 null 60000027 60000027 114202984 60000027 null 60000027 60000027 114156031 60000027 null 60000027 60000027 103035125 60000027 null 60000027 60000027 106483728 60000027 null 60000027 60000027 106936439 60000027 null 60000027 60000027 126177098 60000027 null 60000027 60000027 103035116 60000027 null 60000027 60000027 106146977 60000027 null 60000027 60000027 113857772 60000027 null 60000027 60000027 103035118 60000027 null 60000027 60000027 103035111 60000027 null 60000027 60000027 103035117 60000027 null 60000027 60000027 125866080 60000027 null 60000027 60000027 106902853 60000027 null 60000027 60000027 125865725 60000027 null 60000027 60000027 124820720 60000027 null 60000027 60000027 125865961 60000027 null 60000027 60000027 125865887 60000027 null 60000027 60000027 114450524 60000027 null 60000027 60000027 106936440 60000027 null 60000027 60000027 118219740 60000027 null 60000027 60000027 108045255 60000027 null 60000027 60000027 103035122 60000027 null 60000027 60000027 107959373 60000027 null 60000027 60000027 125865446 60000027 null 60000027 60000027 103035113 60000027 null 60000027 60000027 125866025 60000027 null 60000027 60000027 105520429 60000027 null 60000027 60000027 125866023 60000027 null 60000027 60000027 125865443 60000027 null 60000027 60000027 114545997 60000027 null 60000027 60000027 60000027 60000027 null 60000027 60000027 119774456 60000027 null 60000027 60000027 125865587 60000027 null 60000027 60000027 125865888 60000027 null 60000027 60000027 106936438 60000027 null 60000027 60000027 119629621 60000027 null 60000027 60000027 109702401 60000027 null 60000027 60000027 103035121 60000027 null 60000027 60000027 116521488 60000027 null 60000027 60000027 108134393 60000027 null 60000027 60000027 125865442 60000027 null 60000027 60000027 125865889 60000027 null 60000027 60000027 126177099 60000027 null 60000027 60000027 116323654 60000027 null 60000027 60000027 125865720 60000027 null 60000027 60000027 106810721 60000027 null 60000027 60000027 123077533 60000027 null 60000027 60000027 108388592 60000027 null 60000027 60000027 125865590 60000027 null 60000027 60000027 110908040 60000027 null 60000027 60000027 103035110 60000027 null 60000027 60000027 125865721 60000027 null 60000027 60000027 128460063 60000027 null 60000027 60000027 112919916 60000027 null 60000027 60000027 106570589 60000027 null 60000027 60000027 125865445 60000027 null 60000027 60000027 123461275 60000027 null 60000027 60000027 114549264 60000027 null 60000027 60000027 125865818 60000027 null 60000027 60000027 118226097 60000027 null 60000027 60000027 118016425 60000027 null 60000027 60000027 125865820 60000027 null 60000027 60000027 103035112 60000027 null 60000027 60000027 107576529 60000027 null 60000027 60000027 125866082 60000027 null 60000027 60000027 103035126 60000027 null 60000027 60000027 125865817 60000027 null 60000027 6000002

In [0]:
parent_final = parent_2.select('afid','parent_afid')
parent_final.display()

afid parent_afid 103035115 60000027 125865588 60000027 107099789 60000027 103035114 60000027 125865724 60000027 105302540 60000027 103035124 60000027 125865723 60000027 125865444 60000027 125865722 60000027 107576527 60000027 103035123 60000027 103035119 60000027 112190034 60000027 114537697 60000027 113800358 60000027 125865589 60000027 122906263 60000027 121113920 60000027 107576528 60000027 125866024 60000027 125865819 60000027 125865821 60000027 125866081 60000027 126360461 60000027 125865719 60000027 114202984 60000027 114156031 60000027 103035125 60000027 106483728 60000027 106936439 60000027 126177098 60000027 103035116 60000027 106146977 60000027 113857772 60000027 103035118 60000027 103035111 60000027 103035117 60000027 125866080 60000027 106902853 60000027 125865725 60000027 124820720 60000027 125865961 60000027 125865887 60000027 114450524 60000027 106936440 60000027 118219740 60000027 108045255 60000027 103035122 60000027 107959373 60000027 125865446 60000027 103035113 60000027 125866025 60000027 105520429 60000027 125866023 60000027 125865443 60000027 114545997 60000027 60000027 60000027 119774456 60000027 125865587 60000027 125865888 60000027 106936438 60000027 119629621 60000027 109702401 60000027 103035121 60000027 116521488 60000027 108134393 60000027 125865442 60000027 125865889 60000027 126177099 60000027 116323654 60000027 125865720 60000027 106810721 60000027 123077533 60000027 108388592 60000027 125865590 60000027 110908040 60000027 103035110 60000027 125865721 60000027 128460063 60000027 112919916 60000027 106570589 60000027 125865445 60000027 123461275 60000027 114549264 60000027 125865818 60000027 118226097 60000027 118016425 60000027 125865820 60000027 103035112 60000027 107576529 60000027 125866082 60000027 103035126 60000027 125865817 60000027 114063503 60000027 106170824 60000027 103035120 60000027 127772984 60000027 103035367 60000035 103035365 60000035 103035370 60000035 106177616 60000035 116636451 60000035 108180138 60000035 103035360 60000035 103035354 60000035 60000035 60000035 103035358 60000035 103035357 60000035 103035353 60000035 118965332 60000035 119859752 60000035 103035366 60000035 116566667 60000035 116346307 60000035 103035356 60000035 103035364 60000035 114344029 60000035 114067201 60000035 103035362 60000035 103035355 60000035 118965331 60000035 103035371 60000035 103035368 60000035 128414031 60000035 117898642 60000035 120463241 60000035 103035359 60000035 118603812 60000035 113431186 60000035 122085983 60000035 122175321 60000035 125686706 60000035 126575643 60000035 120701644 60000071 115613983 60000071 103037633 60000071 103037630 60000071 109160891 60000071 105251920 60000071 103037595 60000071 118841640 60000071 103037627 60000071 126071145 60000071 103037604 60000071 114572223 60000071 125322490 60000071 106963979 60000071 116750404 60000071 100301169 60000071 124741310 60000071 103037616 60000071 124738176 60000071 103037614 60000071 103037597 60000071 105500079 60000071 103037625 60000071 110926336 60000071 103037618 60000071 127166255 60000071 103037603 60000071 124738172 60000071 106763067 60000071 103037629 60000071 124738175 60000071 115601446 60000071 107243920 60000071 103037609 60000071 115101740 60000071 103037628 60000071 111215743 60000071 107869610 60000071 106763068 60000071 108147770 60000071 122044390 60000071 103037623 60000071 107090181 60000071 103037632 60000071 116664227 60000071 103037599 60000071 114094360 60000071 124738171 60000071 110232961 60000071 103037602 60000071 112742315 60000071 109467255 60000071 123409444 60000071 125065016 60000071 60000071 60000071 116784976 60000071 124741309 60000071 108558869 60000071 118724100 60000071 103037598 60000071 124738169 60000071 103037611 60000071 105746043 60000071 103037624 60000071 112295695 60000071 103037605 60000071 103037606 60000071 105248334 60000071 103037608 60000071 103037620 60000071 103037615 60000071 108599825 60000071 124738173 60000071 103037612 60000071 103037622 60000071 115290458 60000

In [0]:
parent_final.write.option("header", "true").csv('s3://elsevier-fcads-icsrlab-databricks/custom/proj_030_facmob/aff_parent_scival_final.csv')

In [0]:
read_test = (
    spark.read.format("csv")
    .option("header", "true")
    .load(
        "s3://elsevier-fcads-icsrlab-databricks/custom/proj_030_facmob/aff_parent_scival_final.csv"
    )
)
display(read_test.sort('afid'))

afid parent_afid 100242043 60017717 100242044 60017717 100242045 60017717 100242046 60017717 100242047 60017717 100242048 60017717 100242049 60017717 100242050 60017717 100242051 60017717 100242052 60017717 100242053 60017717 100242054 60017717 100242055 60017717 100242059 60017717 100242060 60017717 100242061 60017717 100242062 60017717 100242063 60017717 100242064 60017717 100242065 60017717 100242066 60017717 100242067 60017717 100242068 60017717 100242069 60017717 100242070 60017717 100242071 60017717 100242072 60017717 100242073 60017717 100242074 60017717 100242075 60017717 100242076 60017717 100242077 60017717 100242078 60017717 100242079 60017717 100242080 60017717 100242081 60017717 100242082 60017717 100242083 60017717 100242084 60017717 100242085 60017717 100242086 60017717 100242087 60017717 100242088 60017717 100242089 60017717 100242090 60017717 100242091 60017717 100242092 60017717 100242093 60017717 100242094 60017717 100242095 60017717 100242096 60017717 100242097 60017717 100242098 60017717 100242099 60017717 100242100 60017717 100242101 60017717 100242102 60017717 100242103 60017717 100242104 60017717 100242105 60017717 100242106 60017717 100242107 60017717 100242108 60017717 100242110 60017717 100242118 60017717 100242127 60017717 100242128 60017717 100242132 60017717 100242133 60017717 100242134 60017717 100242135 60017717 100242136 60017717 100242137 60017717 100242138 60017717 100242139 60017717 100242140 60017717 100242141 60017717 100242170 60032179 100242171 60032179 100242172 60032179 100242173 60032179 100242174 60032179 100242175 60032179 100242176 60032179 100242177 60032179 100242178 60032179 100242179 60032179 100242180 60032179 100242181 60032179 100242182 60032179 100242183 60032179 100242184 60032179 100242185 60032179 100242186 60032179 100242187 60032179 100242188 60032179 100242189 60032179 100242190 60032179 100242191 60032179 100242192 60032179 100242193 60032179 100242200 60032179 100242201 60032179 100242202 60032179 100242203 60032179 100242204 60032179 100242205 60032179 100242206 60032179 100242234 60001423 100242235 60001423 100242236 60001423 100242237 60001423 100242238 60001423 100242239 60001423 100242240 60001423 100242241 60001423 100242242 60001423 100242243 60001423 100242244 60001423 100242245 60001423 100242246 60001423 100242247 60001423 100242248 60001423 100242249 60001423 100242250 60001423 100242251 60001423 100242252 60001423 100242253 60001423 100242254 60001423 100242255 60001423 100242256 60001423 100242257 60001423 100242260 60001423 100242261 60001423 100242314 60024324 100242325 60024324 100242326 60024324 100242335 60015950 100242337 60015950 100242338 60015950 100242339 60015950 100242340 60015950 100242341 60015950 100242342 60015950 100242343 60015950 100242345 60015950 100242346 60015950 100242347 60015950 100242348 60015950 100242349 60015950 100242350 60015950 100242351 60015950 100242352 60015950 100242353 60015950 100242354 60015950 100242364 60015950 100242365 60015950 100242366 60015950 100242367 60015950 100242376 60015950 100242377 60015950 100242378 60015950 100242379 60015950 100242387 60023691 100242388 60023691 100242389 60023691 100242390 60023691 100242392 60023691 100242396 60023691 100242398 60023691 100242399 60023691 100242400 60023691 100242401 60023691 100242402 60023691 100242403 60023691 100242408 60023691 100242409 60023691 100242410 60023691 100242411 60023691 100242412 60023691 100242414 60023691 100242415 60023691 100242416 60023691 100242418 60024613 100242419 60019674 100242420 60019674 100242421 60019674 100242422 60019674 100242423 60019674 100242424 60019674 100242425 60019674 100242426 60019674 100242427 60019674 100242428 60019674 100242429 60019674 100242430 60019674 100242431 60019674 100242432 60019674 100242433 60019674 100242434 60019674 100242435 60019674 100242436 60019674 100242437 60019674 100242438 60019674 100242439 60019674 100242440 60019674 100242441 60019674 100242442 60019674 100242443 60019674 100242444 60